# Basic download and plotting with python
This notebook show how the data can be dowloaded/plotted from python

In [ ]:
# general import, and set download path
import bokeh.io
bokeh.io.output_notebook()
import geoviews as gv
import geoviews.feature as gf
gv.extension('bokeh','matplotlib')
import pandas as pd
import xarray as xr
import rasterio as rio
import rioxarray # geospatial extension for xarray
import os
import matplotlib.pyplot as plt
import cartopy.crs as ccrs
import cartopy
from tqdm.auto import tqdm


download_path="/tmp/cyclobs"
os.makedirs(download_path,exist_ok=True)

In [ ]:
# make the resquest using cyclobs api, and store the result in a pandas dataframe
request_url="https://cyclobs.ifremer.fr/app/api/getData?sid=al122017&instrument=C-Band_SAR&product_type=gridded&include_cols=all"
df_request = pd.read_csv(request_url)


# add download path
df_request['data_url'] = df_request['data_url'].apply(lambda x: x.replace("_ll_gd", "_gd"))
df_request['path'] = df_request['data_url'].map(lambda x : os.path.join(download_path,os.path.basename(x)))
df_request['path'].iloc[0]

In [ ]:
# download 'data_url' to 'path' with wget, and read files
projection=ccrs.Mercator()
datasets = []
for idx,entry in tqdm(df_request.iterrows(),total=df_request.shape[0]):
    ret = os.system('cd %s ; wget -N  %s' % (os.path.dirname(entry['path']),entry['data_url']))
    if ret == 0 : 
        ds = xr.open_dataset(entry['path'])
        datasets.append( ds.rio.reproject(projection.proj4_params))
        
    else:
        datasets.append(None) # error fetching file
datasets[0]['wind_speed']

In [ ]:
gv_list=[gf.coastline.opts(projection=projection)]
for ds in datasets:
    gv_list.append(gv.Image(ds['wind_speed'].squeeze()[::5,::5],crs=projection).opts(cmap='jet',tools=['hover']))
    
gv.Overlay(gv_list).options(width=800, height=500)

# Notebook installation

To run and customize this notebook on your computer, you will need to install some packages with conda:


```
conda create -n cyclobs python=3 cartopy

conda activate cyclobs

pip install xarray netcdf4 geoviews pandas rioxarray tqdm ipywidgets

wget https://gitlab.ifremer.fr/cyclobs/user_manual/-/raw/master/user_manual.ipynb
```

To start the notebook :

`jupyter notebook`

